In [1]:
import os
import numpy as np
import pandas as pd
import plotly.express as px
import plotly.io as pio
import plotly.graph_objects as go
import geopandas as gpd
from geojson import Feature, FeatureCollection
from dotenv import load_dotenv

load_dotenv()

In [2]:
cities = gpd.read_parquet("../eterna-primavera/aux_data/valle_aburra.parquet")

In [3]:
def get_selection_series(cities, selected_city):
    return cities["MPIO_CDPMP"] == selected_city

In [4]:
# Would like this map to have population per area
def gdf_to_json(
    gdf: gpd.GeoDataFrame,
    id_col: str,
    geometry_col: str,
    # value_field: str,
):
    list_features = []
    for _, row in gdf.iterrows():
        feature = Feature(
            geometry=row[geometry_col],
            id=row[id_col],
            # properties={"value": row[value_field]},
        )
        list_features.append(feature)
    feat_collection = FeatureCollection(list_features)
    return feat_collection

In [20]:
geojson_obj = gdf_to_json(cities, "MPIO_CDPMP", "geometry")
selection = get_selection_series(cities, "05001")

fig = px.choropleth_mapbox(
        cities,
        geojson=geojson_obj,
        locations="MPIO_CDPMP",
        color=selection,
        color_discrete_map={True: "#0850BC", False: "#F4F4F4"},
        mapbox_style="carto-positron",
        zoom=9,
        center = {"lat": 6.240833, "lon": -75.530553},
        # TODO: Add extra info and show get_name() on hover
        # hover_data={
        #     "size": True,
        #     "h3": False
        # }
)

fig = fig.update_layout(
    mapbox_style=os.environ["MAPBOX_STYLE"],
    mapbox_accesstoken=os.environ["MAPBOX_TOKEN"],
    margin=dict(l=0, r=0, t=0, b=0),
    uirevision="Don't change"  # this option forces zoom to stay the same when data is updated)
)

In [21]:
fig